# 1. Requirements Breakdown & Planning

## Define Objectives:

- Detect and track players, ball, and game events.
- Extract tactical metrics: ball possession, pressure zones, team formations, match tempo.
- Support both real-time and offline (recorded footage) analysis.
- Provide structured outputs for visualization and integration with scouting/coaching tools.

## System Components:

### Data Collection & Preprocessing:
- Gather annotated soccer video clips.
- Preprocess footage (stabilization, cropping, color normalization).
- Field segmentation for tactical zones.

### Computer Vision & Deep Learning Models:
- Object detection (players and ball) using models like YOLO or Faster R-CNN.
- Tracking (e.g., SORT, DeepSORT) to follow objects across frames.

### Tactical Analysis Module:
- Calculate ball possession and pressure zones.
- Infer team formations and analyze match tempo using motion dynamics.

### Integration & Output:
- Structure outputs for visual dashboards and reporting.
- Provide APIs or export functions for integration.

## Optimization & Adaptability:

- Tune models for various camera angles and match conditions.
- Optimize for real-time performance via model quantization or GPU acceleration.


# 2. Execution Plan

- Step 1: Data Preparation

    - Create scripts to preprocess video input.
    - Develop field segmentation routines to divide the pitch into tactical zones.

- Step 2: Model Development

    - Build or integrate a pre-trained deep learning model for detecting players and the ball.
    - Develop a tracking module to link detections over frames.

- Step 3: Tactical Metrics Extraction

    - Use the tracking data to compute ball possession statistics.
    - Analyze player positions to define pressure zones and team formations.
    - Monitor movement speed and direction to approximate match tempo.

- Step 4: Visualization & Reporting

    - Build routines to overlay detection results and tactical zones on video frames.
    - Generate structured reports (e.g., JSON, CSV) for further use in integration.

- Step 5: Optimization & Real-time Integration

    - Profile the system and apply optimizations (GPU, multithreading).
    - Ensure the pipeline handles streaming input and recorded footage.

- Step 6: Testing & Evaluation

    - Write unit tests for each module.
    - Evaluate the accuracy and efficiency on sample footage.

-------------------------------------------------------------

# Good team detection - manual coloring

In [5]:
import os
import cv2
import numpy as np
from ultralytics import YOLO
from deep_sort_realtime.deepsort_tracker import DeepSort

def load_preprocessed_frames(filename):
    data = np.load(filename, allow_pickle=True)
    frames = list(data['frames'])
    fps = float(data['fps'])
    print(f"Loaded {len(frames)} frames from {filename}")
    return frames, fps

def detect_objects(frame, model):
    """Detect players using YOLOv8"""
    results = model([frame], conf=0.25)
    
    detections = []
    for box in results[0].boxes:
        xyxy = box.xyxy[0].cpu().numpy().astype(int)
        x, y, x2, y2 = xyxy
        w = x2 - x
        h = y2 - y
        cls_idx = int(box.cls.cpu().numpy()[0])
        label = model.names[cls_idx]
        
        if label == 'person':
            detections.append({
                "label": label,
                "bbox": [x, y, w, h],
                "confidence": float(box.conf[0])
            })
        elif label == 'sports ball':
            detections.append({
                "label": label,
                "bbox": [x, y, w, h],
                "confidence": float(box.conf[0])
            })
    
    return detections

def analyze_jersey_color(frame, bbox):
    """Extract jersey color info with visualization"""
    x, y, w, h = bbox
    
    # Extract jersey area (top part of the person)
    jersey_y1 = max(0, int(y + h * 0.15))  # Start at 15% from top
    jersey_y2 = min(frame.shape[0]-1, int(y + h * 0.45))  # End at 45%
    jersey_x1 = max(0, x)
    jersey_x2 = min(frame.shape[1]-1, x + w)
    
    # Safety check
    if jersey_y1 >= jersey_y2 or jersey_x1 >= jersey_x2:
        return None, None, None
    
    # Get jersey ROI
    jersey_roi = frame[jersey_y1:jersey_y2, jersey_x1:jersey_x2]
    
    if jersey_roi.size == 0:
        return None, None, None
    
    # Calculate average color in HSV space for better color analysis
    try:
        hsv_roi = cv2.cvtColor(jersey_roi, cv2.COLOR_BGR2HSV)
        avg_h = np.mean(hsv_roi[:,:,0])
        avg_s = np.mean(hsv_roi[:,:,1])
        avg_v = np.mean(hsv_roi[:,:,2])
        hsv_avg = (avg_h, avg_s, avg_v)
        
        # Also get BGR average for visualization
        avg_b = np.mean(jersey_roi[:,:,0])
        avg_g = np.mean(jersey_roi[:,:,1])
        avg_r = np.mean(jersey_roi[:,:,2])
        bgr_avg = (avg_b, avg_g, avg_r)
        
        # Create a visualization of the jersey region
        jersey_vis = jersey_roi.copy()
        
        return hsv_avg, bgr_avg, jersey_vis
    except Exception as e:
        print(f"Error in jersey analysis: {e}")
        return None, None, None

def classify_team(hsv_avg, bgr_avg):
    """
    Classify team based on jersey color.
    Return team name, confidence, and display color
    """
    if hsv_avg is None:
        return "Unknown", 0, (0, 255, 0)
    
    h, s, v = hsv_avg
    
    # Real Madrid: Higher brightness, various saturation levels
    if v > 115 and s < 90:  # Based on your samples
        return "Real Madrid", 85, (255, 255, 255)
    
    # Referee: Very specific hue range around 58-60
    if 55 < h < 62 and 120 < s < 140 and 100 < v < 115:
        return "Referee", 90, (0, 255, 255)
    
    # Barcelona: Higher saturation, lower brightness
    if s > 100 and v < 120:
        return "FC Barcelona", 80, (160, 0, 140)
    
    # Additional classification for brighter Real Madrid jerseys
    if v > 150:
        return "Real Madrid", 70, (255, 255, 255)
    
    # Fallback
    return "Unknown", 0, (0, 255, 0)

def visualize_teams(frame, detections):
    """Draw players with team info and color coding"""
    output = frame.copy()
    
    # Count teams
    rm_count = 0
    barca_count = 0
    unknown_count = 0
    
    # Process each detection
    for det in detections:
        try:
            if det["label"] != "person":
                continue
                
            # Ensure all bbox values are integers
            bbox = det["bbox"]
            if len(bbox) != 4:
                print(f"Warning: Invalid bbox format: {bbox}")
                continue
                
            x, y, w, h = [int(val) if val is not None else 0 for val in bbox]
            
            # Extract and analyze jersey color
            hsv_avg, bgr_avg, jersey_vis = analyze_jersey_color(frame, det["bbox"])
            
            # Classify team
            team, confidence, color = classify_team(hsv_avg, bgr_avg)
            
            # Count teams
            if team == "Real Madrid":
                rm_count += 1
            elif team == "FC Barcelona":
                barca_count += 1
            else:
                unknown_count += 1
            
            # Draw bounding box
            cv2.rectangle(output, (x, y), (x+w, y+h), color, 2)
            
            # Draw color sample
            if bgr_avg is not None:
                sample_color = tuple(map(int, bgr_avg))
                cv2.rectangle(output, (x+w+5, y), (x+w+25, y+20), sample_color, -1)
            
            # Draw team name and HSV values
            if hsv_avg is not None:
                h_val, s, v = hsv_avg  # Use h_val to avoid shadowing h (height)
                text = f"{team} ({confidence:.0f}%)"
                
                # Safe text positions with explicit integer coordinates
                text_x, text_y = int(x), max(int(y)-8, 0)
                hsv_text_x, hsv_text_y = int(x), int(y+h+15)
                
                # Safely draw text
                cv2.putText(output, text, (text_x, text_y), 
                           cv2.FONT_HERSHEY_SIMPLEX, 0.5, color, 2)
                
                hsv_text = f"H:{h_val:.0f} S:{s:.0f} V:{v:.0f}"
                cv2.putText(output, hsv_text, (hsv_text_x, hsv_text_y), 
                           cv2.FONT_HERSHEY_SIMPLEX, 0.4, (255,255,255), 1)
                
            # Show jersey region with rectangle
            if jersey_vis is not None:
                jersey_y1 = int(y + h * 0.15)
                jersey_y2 = int(y + h * 0.45)
                cv2.rectangle(output, (x, jersey_y1), (x+w, jersey_y2), (0, 255, 255), 1)
        except Exception as e:
            print(f"Error processing detection: {e}")
            continue
    
    # Draw team counts - ensure integer coordinates
    try:
        cv2.putText(output, f"Real Madrid: {rm_count}", (10, 30), 
                   cv2.FONT_HERSHEY_SIMPLEX, 0.7, (255, 255, 255), 2)
        cv2.putText(output, f"FC Barcelona: {barca_count}", (10, 60), 
                   cv2.FONT_HERSHEY_SIMPLEX, 0.7, (160, 0, 140), 2)
        cv2.putText(output, f"Unknown: {unknown_count}", (10, 90), 
                   cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0, 255, 0), 2)
    except Exception as e:
        print(f"Error drawing team counts: {e}")
    
    return output


if __name__ == "__main__":
    # Path to color frames
    frames_filename = "preprocessed_frames_P1_colored.npz"
    
    # Create window
    cv2.namedWindow("Team Classification", cv2.WINDOW_NORMAL)
    cv2.resizeWindow("Team Classification", 960, 540)
    
    # Load frames
    if os.path.exists(frames_filename):
        frames, fps = load_preprocessed_frames(frames_filename)
        print(f"Frame shape: {frames[0].shape}")
    else:
        print("Color frames file not found!")
        exit(1)
    
    # Load YOLOv8 for detection
    model = YOLO('yolov8n.pt')
    
    # Create video writer
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out_writer = cv2.VideoWriter("team_classification.mp4", fourcc, fps, 
                                (frames[0].shape[1], frames[0].shape[0]))
    
    print("Processing frames...")
    # Process frames
    for idx, frame in enumerate(frames):
        try:
            # Skip frames for faster processing during testing
            if idx % 5 != 0:
                continue
                
            # Detect players
            detections = detect_objects(frame, model)
            
            # Visualize with team classification
            output = visualize_teams(frame, detections)
            
            # Write and display
            out_writer.write(output)
            display_frame = cv2.resize(output, (960, 540))
            cv2.imshow("Team Classification", display_frame)
            
            # Process UI events
            key = cv2.waitKey(1)
            if key == 27:  # ESC
                break
            
            # Progress update
            if idx % 25 == 0:
                print(f"Processed frame {idx}")
                
        except Exception as e:
            print(f"Error on frame {idx}: {e}")
            import traceback
            traceback.print_exc()
            continue
            
    # Clean up
    out_writer.release()
    cv2.destroyAllWindows()
    print("Complete! Output saved to team_classification.mp4")

Loaded 9501 frames from preprocessed_frames_P1_colored.npz
Frame shape: (360, 640, 3)
Processing frames...

0: 384x640 3 persons, 90.2ms
Speed: 2.7ms preprocess, 90.2ms inference, 0.7ms postprocess per image at shape (1, 3, 384, 640)
Processed frame 0

0: 384x640 3 persons, 73.1ms
Speed: 1.6ms preprocess, 73.1ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 10 persons, 1 sports ball, 76.4ms
Speed: 1.8ms preprocess, 76.4ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 12 persons, 2 motorcycles, 1 sports ball, 73.5ms
Speed: 1.4ms preprocess, 73.5ms inference, 1.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 15 persons, 2 motorcycles, 1 sports ball, 66.9ms
Speed: 1.2ms preprocess, 66.9ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 15 persons, 2 motorcycles, 1 sports ball, 82.5ms
Speed: 1.1ms preprocess, 82.5ms inference, 1.8ms postprocess per image at shape (1, 3, 384, 640)
Proc

---------------------

# K-means clustering Teams

In [2]:
import os
import cv2
import numpy as np
from ultralytics import YOLO
from deep_sort_realtime.deepsort_tracker import DeepSort
from collections import defaultdict
from sklearn.cluster import KMeans

def load_preprocessed_frames(filename):
    """Load preprocessed video frames from a .npz file"""
    data = np.load(filename, allow_pickle=True)
    frames = list(data['frames'])
    fps = float(data['fps'])
    print(f"Loaded {len(frames)} frames from {filename}")
    return frames, fps

def detect_objects(frame, model):
    """Detect players using YOLOv8"""
    results = model([frame], conf=0.25)
    
    detections = []
    for box in results[0].boxes:
        xyxy = box.xyxy[0].cpu().numpy().astype(int)
        x, y, x2, y2 = xyxy
        w = x2 - x
        h = y2 - y
        cls_idx = int(box.cls.cpu().numpy()[0])
        label = model.names[cls_idx]
        
        if label == 'person':
            detections.append({
                "label": label,
                "bbox": [x, y, w, h],
                "confidence": float(box.conf[0])
            })
        elif label == 'sports ball':
            detections.append({
                "label": label,
                "bbox": [x, y, w, h],
                "confidence": float(box.conf[0])
            })
    
    return detections

def analyze_jersey_color_kmeans(frame, bbox, k=3):
    """Extract jersey colors using k-means clustering with optimized ROI"""
    x, y, w, h = [int(val) for val in bbox]
    
    # Extract jersey area with adjusted parameters to focus more on central torso
    jersey_y1 = max(0, int(y + h * 0.20))  # Start a bit lower (was 0.15)
    jersey_y2 = min(frame.shape[0]-1, int(y + h * 0.55))  # Go lower to catch more jersey (was 0.45)
    
    # Narrow horizontally to avoid arms/surroundings
    margin = int(w * 0.10)  # 10% margin from each side
    jersey_x1 = max(0, x + margin)
    jersey_x2 = min(frame.shape[1]-1, x + w - margin)
    
    # Get jersey ROI
    jersey_roi = frame[jersey_y1:jersey_y2, jersey_x1:jersey_x2]
    
    if jersey_roi.size == 0 or jersey_roi.shape[0] < 5 or jersey_roi.shape[1] < 5:
        return None, None, None, None
        
    try:
        # Reshape the jersey ROI for clustering
        pixels = jersey_roi.reshape(-1, 3).astype(np.float32)
        
        # Apply k-means clustering to find dominant colors
        kmeans = KMeans(n_clusters=k, random_state=0, n_init=10)
        kmeans.fit(pixels)
        
        # Get dominant colors and their proportions
        colors = kmeans.cluster_centers_.astype(np.uint8)
        labels = kmeans.labels_
        counts = np.bincount(labels)
        
        # Sort colors by frequency (most common first)
        dominant_idx = np.argsort(-counts)
        dominant_colors = [colors[i] for i in dominant_idx]
        color_percentages = [counts[i]/len(labels)*100 for i in dominant_idx]
        
        # Convert to HSV for better analysis
        hsv_colors = [cv2.cvtColor(np.uint8([[color]]), cv2.COLOR_BGR2HSV)[0][0] for color in dominant_colors]
        
        # Create visualization
        vis_roi = jersey_roi.copy()
        color_vis = np.zeros((50, jersey_roi.shape[1], 3), dtype=np.uint8)
        
        # Add color bars showing dominant colors
        segment_width = jersey_roi.shape[1] // len(dominant_colors)
        for i, (color, pct) in enumerate(zip(dominant_colors, color_percentages)):
            start_x = i * segment_width
            end_x = (i + 1) * segment_width if i < len(dominant_colors) - 1 else jersey_roi.shape[1]
            color_vis[:, start_x:end_x] = color
            
        # Add percentage text
        for i, pct in enumerate(color_percentages):
            x_pos = int((i + 0.5) * segment_width)
            # Safe color sum calculation
            color_sum = int(dominant_colors[i][0]) + int(dominant_colors[i][1]) + int(dominant_colors[i][2])
            text_color = (0,0,0) if color_sum > 380 else (255,255,255)
            cv2.putText(color_vis, f"{pct:.1f}%", (x_pos-20, 30), 
                      cv2.FONT_HERSHEY_SIMPLEX, 0.4, text_color, 1)
        
        # Combine original ROI with visualization
        jersey_vis = np.vstack([vis_roi, color_vis])
        
        return hsv_colors, dominant_colors, color_percentages, jersey_vis
        
    except Exception as e:
        print(f"Error in k-means clustering: {e}")
        return None, None, None, None

def safe_color_distance(h, ex_h, s, ex_s, v, ex_v):
    """Calculate color distance with safety checks to avoid overflow errors"""
    # Convert to Python numbers to avoid NumPy overflow warnings
    h, ex_h = float(h), float(ex_h)
    s, ex_s = float(s), float(ex_s)
    v, ex_v = float(v), float(ex_v)
    
    # Calculate color distance in HSV space (with wraparound for hue)
    h_dist = min(abs(h - ex_h), 180 - abs(h - ex_h)) / 180.0
    s_dist = abs(s - ex_s) / 255.0
    v_dist = abs(v - ex_v) / 255.0
    
    # Combined weighted distance (hue matters most, then saturation, then value)
    distance = h_dist * 0.6 + s_dist * 0.3 + v_dist * 0.1
    
    return distance

def classify_team_kmeans(hsv_colors, bgr_colors, percentages, use_exemplars=True):
    """
    Improved team classification with reduced referee bias and field color rejection
    """
    if hsv_colors is None or not hsv_colors:
        return "Unknown", 0, (0, 255, 0)
    
    # Debug mode
    debug = True
    
    # Team exemplar colors - adjusted weights to reduce referee bias
    EXEMPLARS = {
        "real_madrid": [
            # White jersey (slightly increased weights)
            {"hsv": (0, 0, 230), "weight": 1.05},   # Pure white
            {"hsv": (80, 10, 220), "weight": 0.95}, # Off-white
            {"hsv": (30, 20, 210), "weight": 0.9}   # Additional off-white shade
        ],
        "barcelona": [
            # Blue/burgundy (slightly increased weights)
            {"hsv": (105, 100, 70), "weight": 1.05},  # Dark blue
            {"hsv": (0, 120, 80), "weight": 0.95},    # Burgundy
            {"hsv": (170, 120, 80), "weight": 0.95}   # Burgundy (other end)
        ],
        "referee": [
            # Black or yellow - REDUCED weights
            {"hsv": (0, 0, 20), "weight": 0.9},      # Black - decreased weight
            {"hsv": (0, 0, 40), "weight": 0.8},      # Dark gray - decreased
            {"hsv": (30, 150, 120), "weight": 0.9},  # Yellow - decreased
            {"hsv": (25, 170, 140), "weight": 0.8}   # Yellow variant - decreased
        ]
    }
    
    # Team color signatures
    WHITE = {
        "h_range": (0, 180),     
        "s_max": 45,
        "v_min": 180
    }
    
    # Barcelona colors
    BARCA = {
        "primary_blue": {
            "h_range": [(95, 120)],
            "s_min": 80,
            "v_range": (30, 85)
        },
        "primary_red": {
            "h_range": [(0, 10), (170, 180)],
            "s_min": 100,
            "v_range": (40, 85)
        }
    }
    
    # Referee colors - stricter criteria
    REFEREE = {
        "black": {"v_max": 35, "s_max": 40},      # Stricter darkness requirement
        "yellow": {
            "h_range": (28, 33),                  # Narrower yellow hue range
            "s_range": (140, 190),                # Stricter saturation range
            "v_range": (110, 150)                 # Stricter value range
        }
    }
    
    # Field/grass color range
    FIELD = {
        "h_range": (35, 85),    # Green hue range
        "s_min": 60,            # Minimum saturation for field green
        "v_range": (30, 150)    # Value range for field green
    }
    
    # Initialize scores
    real_madrid_score = 0
    barcelona_score = 0
    referee_score = 0
    
    # Sort colors by percentage (most dominant first)
    sorted_indices = sorted(range(len(percentages)), key=lambda i: percentages[i], reverse=True)
    sorted_hsv = [hsv_colors[i] for i in sorted_indices]
    sorted_bgr = [bgr_colors[i] for i in sorted_indices]
    sorted_pct = [percentages[i] for i in sorted_indices]
    
    # Check for field green as dominant color - FIELD COLOR REJECTION
    if sorted_hsv and len(sorted_hsv) > 0:
        h, s, v = sorted_hsv[0]
        if (FIELD["h_range"][0] <= h <= FIELD["h_range"][1] and 
            s >= FIELD["s_min"] and 
            FIELD["v_range"][0] <= v <= FIELD["v_range"][1]):
            
            # If dominant color is grass-like and over 50%, reduce confidence
            if sorted_pct[0] > 50:
                # Apply a field penalty factor based on how much green is present
                field_penalty = min(0.8, sorted_pct[0] / 100)
                
                if debug:
                    print(f"Field green detected ({sorted_pct[0]:.1f}%) - reducing confidence")
                
                # Return unknown for very strong field green (over 70%)
                if sorted_pct[0] > 70:
                    return "Unknown", 0, (0, 255, 0)
    
    # Weight factors based on color dominance
    dominance_weights = [1.0, 0.5, 0.3]
    
    # EXEMPLAR COMPARISON
    if use_exemplars:
        for i, (hsv, bgr, pct) in enumerate(zip(sorted_hsv, sorted_bgr, sorted_pct)):
            h, s, v = hsv
            
            # Apply dominance weight
            dominance_weight = dominance_weights[i] if i < len(dominance_weights) else 0.1
            weight = (pct / 100) * dominance_weight
            
            # FIELD COLOR REJECTION - Skip grass-like colors
            if (FIELD["h_range"][0] <= h <= FIELD["h_range"][1] and 
                s >= FIELD["s_min"] and 
                FIELD["v_range"][0] <= v <= FIELD["v_range"][1]):
                if debug and pct > 30:
                    print(f"Skipping field green: H:{h:.1f} S:{s:.1f} V:{v:.1f} - {pct:.1f}%")
                continue
            
            if debug and pct > 30:
                print(f"Dominant color: H:{h:.1f} S:{s:.1f} V:{v:.1f} - {pct:.1f}%")
                
            # WHITE DETECTION - for Real Madrid
            if v > 210 and s < 30 and i == 0:
                real_madrid_score += 40 * weight
                continue
                
            # Calculate distance to each exemplar
            for team, exemplars in EXEMPLARS.items():
                for exemplar in exemplars:
                    ex_h, ex_s, ex_v = exemplar["hsv"]
                    
                    distance = safe_color_distance(h, ex_h, s, ex_s, v, ex_v)
                    similarity = max(0, 1.0 - distance)
                    
                    score = similarity * exemplar["weight"] * weight * 100
                    
                    if team == "real_madrid":
                        real_madrid_score += score
                    elif team == "barcelona":
                        barcelona_score += score
                    else:  # referee
                        # Apply a stricter multiplier for referee scores
                        referee_score += score * 0.8  # 20% reduction in referee scores
    
    # TRADITIONAL HSV RANGE ANALYSIS
    major_colors = [(hsv, pct) for hsv, pct in zip(sorted_hsv, sorted_pct) if pct > 30]
    if major_colors:
        for hsv, pct in major_colors:
            h, s, v = hsv
            weight = pct / 100
            
            # SKIP FIELD GREEN COLORS
            if (FIELD["h_range"][0] <= h <= FIELD["h_range"][1] and 
                s >= FIELD["s_min"] and 
                FIELD["v_range"][0] <= v <= FIELD["v_range"][1]):
                continue
            
            # Special case for very dark colors (referee black) - stricter
            if v < 35 and s < 40:  # Stricter than before
                referee_score += (35 - v) * 1.5 * weight  # Reduced multiplier
                continue
            
            # Special case for referee yellow - stricter
            if REFEREE["yellow"]["h_range"][0] <= h <= REFEREE["yellow"]["h_range"][1] and \
               REFEREE["yellow"]["s_range"][0] <= s <= REFEREE["yellow"]["s_range"][1] and \
               REFEREE["yellow"]["v_range"][0] <= v <= REFEREE["yellow"]["v_range"][1]:
                referee_score += 70 * weight  # Reduced from 80
                continue
            
            # White Real Madrid
            if v > WHITE["v_min"] and s < WHITE["s_max"]:
                white_score = min(100, (v - WHITE["v_min"]) * 1.0 + (WHITE["s_max"] - s))
                real_madrid_score += white_score * weight * 0.7  # Increased weight
            
            # Barcelona blue
            for h_min, h_max in BARCA["primary_blue"]["h_range"]:
                if h_min <= h <= h_max and s > BARCA["primary_blue"]["s_min"] and \
                   BARCA["primary_blue"]["v_range"][0] <= v <= BARCA["primary_blue"]["v_range"][1]:
                    blue_score = min(100, (s - BARCA["primary_blue"]["s_min"]) + 30)
                    barcelona_score += blue_score * weight * 0.7  # Increased weight
    
    # Get the highest score
    team_scores = [
        ("Real Madrid", real_madrid_score, (255, 255, 255)),
        ("FC Barcelona", barcelona_score, (160, 0, 140)),
        ("Referee", referee_score, (0, 255, 255))
    ]
    
    # Print debug info
    if debug:
        for team, score, _ in team_scores:
            if score > 10:
                print(f"{team} score: {score:.1f}")
    
    # Choose winner with highest score
    winner = max(team_scores, key=lambda x: x[1])
    team, score, color = winner
    
    # Higher threshold for referee classification
    if team == "Referee" and score < 35:  # Higher threshold for referees
        return "Unknown", 0, (0, 255, 0)
    elif score < 30:  # Standard threshold for teams
        return "Unknown", 0, (0, 255, 0)
    
    return team, score, color

def adjust_team_classifications(detections, classifications):
    """Apply sanity checks to team classifications"""
    # Count teams
    team_counts = defaultdict(int)
    for team, _, _ in classifications:
        team_counts[team] += 1
    
    # Check for unreasonable counts
    total_players = len(classifications)
    max_team_size = min(11, total_players - 1)  # Max players per team in soccer
    max_referee_count = 3  # Maximum 3 referees (one main + two assistants)
    
    # If one team dominates too heavily, adjust classifications
    for team in team_counts:
        if team == "Referee" and team_counts[team] > max_referee_count:
            # Sort by confidence (lowest first)
            sorted_indices = sorted(range(len(classifications)), 
                                   key=lambda i: classifications[i][1] if classifications[i][0] == team else float('inf'))
            
            # Convert excess referees to Unknown
            excess = team_counts[team] - max_referee_count
            for i in range(excess):
                if i < len(sorted_indices):
                    idx = sorted_indices[i]
                    classifications[idx] = ("Unknown", 0, (0, 255, 0))
        
        elif team in ["Real Madrid", "FC Barcelona"] and team_counts[team] > max_team_size:
            # Sort by confidence (lowest first)
            sorted_indices = sorted(range(len(classifications)), 
                                   key=lambda i: classifications[i][1] if classifications[i][0] == team else float('inf'))
            
            # Convert excess players to Unknown
            excess = team_counts[team] - max_team_size
            for i in range(excess):
                if i < len(sorted_indices):
                    idx = sorted_indices[i]
                    classifications[idx] = ("Unknown", 0, (0, 255, 0))
    
    return classifications


def visualize_teams(frame, detections, temporal_consistency=None, show_debug=True):
    """
    Draw players with team info using k-means color clustering
    
    Args:
        frame: Input video frame
        detections: List of player detections
        temporal_consistency: Optional SimpleTemporalConsistency object for smoother classifications
        show_debug: Whether to show detailed debugging info
    """
    output = frame.copy()
    
    # Count teams
    rm_count = 0
    barca_count = 0
    referee_count = 0
    unknown_count = 0
    
    # Store classifications for sanity checks
    classifications = []
    
    # First pass: classify all players
    for det in detections:
        try:
            if det["label"] != "person":
                continue
                
            # Ensure all bbox values are integers
            bbox = det["bbox"]
            if len(bbox) != 4:
                print(f"Warning: Invalid bbox format: {bbox}")
                continue
                
            x, y, w, h = [int(val) if val is not None else 0 for val in bbox]
            
            # Extract and analyze jersey color using k-means
            hsv_colors, bgr_colors, percentages, jersey_vis = analyze_jersey_color_kmeans(frame, det["bbox"])
            
            # Classify team based on dominant colors
            team, confidence, color = classify_team_kmeans(hsv_colors, bgr_colors, percentages)
            
            # Add to temporal consistency if available
            if temporal_consistency is not None:
                frame_idx = det.get("frame_idx", 0)
                temporal_consistency.add_detection(frame_idx, x, y, w, h, team, confidence)
                
                # Check for consistent classification
                consistent_team, avg_conf = temporal_consistency.get_consistent_team(x, y, w, h)
                
                # Use consistent classification if available and confident
                if consistent_team and avg_conf > 40:
                    team = consistent_team
                    confidence = avg_conf
                    # Update color based on team
                    if team == "Real Madrid":
                        color = (255, 255, 255)
                    elif team == "FC Barcelona":
                        color = (160, 0, 140)
                    elif team == "Referee":
                        color = (0, 255, 255)
                    else:
                        color = (0, 255, 0)
            
            # Add to classifications list for sanity checks
            classifications.append((team, confidence, color))
            
            # Store detection for later visualization
            det["team"] = team
            det["confidence"] = confidence
            det["color"] = color
            det["hsv_colors"] = hsv_colors
            det["bgr_colors"] = bgr_colors
            det["jersey_vis"] = jersey_vis
            det["percentages"] = percentages
                
        except Exception as e:
            print(f"Error processing detection: {e}")
            continue
    
    # Sanity check on classifications
    if len(classifications) >= 5:
        adjusted_classifications = adjust_team_classifications(detections, classifications)
        
        # Update detections with adjusted classifications
        for i, (team, confidence, color) in enumerate(adjusted_classifications):
            if i < len(detections) and "team" in detections[i]:
                detections[i]["team"] = team
                detections[i]["confidence"] = confidence
                detections[i]["color"] = color
    
    # Second pass: visualize with corrected classifications
    for det in detections:
        try:
            if det["label"] != "person" or "team" not in det:
                continue
                
            x, y, w, h = [int(val) if val is not None else 0 for val in det["bbox"]]
            team = det["team"]
            confidence = det["confidence"]
            color = det["color"]
            #hsv_colors = det.get("hsv_colors")
            #bgr_colors = det.get("bgr_colors")
            #jersey_vis = det.get("jersey_vis")
            
            # Count teams
            if team == "Real Madrid": rm_count += 1
            elif team == "FC Barcelona": barca_count += 1
            elif team == "Referee": referee_count += 1
            else: unknown_count += 1
            
            # IMPROVED: Draw more elegant bounding box
            cv2.rectangle(output, (x, y), (x+w, y+h), color, 1)  # Reduced thickness
            
            # IMPROVED: Draw team name and confidence more subtly
            #text = f"{team}" if confidence > 70 else f"{team} ({confidence:.0f}%)"
            text = f"{team}"  # Remove confidence display for presentation
            text_x, text_y = int(x), max(int(y)-5, 0)
            
            # Add a small background for better text visibility
            text_size = cv2.getTextSize(text, cv2.FONT_HERSHEY_SIMPLEX, 0.4, 1)[0]
            cv2.rectangle(output, (text_x, text_y-text_size[1]-2), 
                        (text_x+text_size[0], text_y+2), (0,0,0), -1)
            cv2.putText(output, text, (text_x, text_y), 
                       cv2.FONT_HERSHEY_SIMPLEX, 0.4, color, 1)
            
            # IMPROVED: Show jersey region with more elegant rectangle
            jersey_y1 = int(y + h * 0.20)
            jersey_y2 = int(y + h * 0.55)
            margin = int(w * 0.10)
            
            # Use dashed lines for jersey region (more subtle)
            jersey_color = color if team != "Unknown" else (0, 255, 255)
            # Draw dashed rectangle
            dash_length = 5
            for i in range(0, w - 2*margin, dash_length*2):
                # Top line
                pt1 = (x + margin + i, jersey_y1)
                pt2 = (min(x + margin + i + dash_length, x + w - margin), jersey_y1)
                cv2.line(output, pt1, pt2, jersey_color, 1)
                
                # Bottom line
                pt1 = (x + margin + i, jersey_y2)
                pt2 = (min(x + margin + i + dash_length, x + w - margin), jersey_y2)
                cv2.line(output, pt1, pt2, jersey_color, 1)
            
            for i in range(0, jersey_y2 - jersey_y1, dash_length*2):
                # Left line
                pt1 = (x + margin, jersey_y1 + i)
                pt2 = (x + margin, min(jersey_y1 + i + dash_length, jersey_y2))
                cv2.line(output, pt1, pt2, jersey_color, 1)
                
                # Right line
                pt1 = (x + w - margin, jersey_y1 + i)
                pt2 = (x + w - margin, min(jersey_y1 + i + dash_length, jersey_y2))
                cv2.line(output, pt1, pt2, jersey_color, 1)
            

            # IMPROVED: Show HSV values for debugging (more subtle)
            """
            if show_debug and hsv_colors is not None and len(hsv_colors) > 0:
                # Get dominant color HSV
                h, s, v = hsv_colors[0]
                hsv_text = f"H:{h:.0f} S:{s:.0f} V:{v:.0f}"
                # More careful boundary check
                if y + h + 15 < output.shape[0]:  # Check if there's room before calculating
                    text_y = min(y + h + 15, output.shape[0] - 5)
                    # Make HSV text smaller and semi-transparent
                    fontScale = 0.35
                    # Draw with transparency
                    overlay = output.copy()
                    cv2.putText(overlay, hsv_text, (x, text_y), 
                              cv2.FONT_HERSHEY_SIMPLEX, fontScale, (255, 255, 255), 1)
                    # Add overlay with alpha blending
                    alpha = 0.7
                    cv2.addWeighted(overlay, alpha, output, 1-alpha, 0, output)
            
            # Show dominant colors if available
            if bgr_colors is not None and jersey_vis is not None:
                # Scale jersey visualization to appropriate size
                scale = min(0.2, 100 / max(jersey_vis.shape[0], 1))
                vis_h = int(jersey_vis.shape[0] * scale)
                vis_w = int(jersey_vis.shape[1] * scale)
                if vis_h > 0 and vis_w > 0:
                    try:
                        small_vis = cv2.resize(jersey_vis, (vis_w, vis_h))
            
                        # Safer coordinate calculation
                        roi_y = max(0, min(y + h + 20, output.shape[0] - vis_h - 1))
                        roi_x = max(0, min(x, output.shape[1] - vis_w - 1))
            
                        # Extra safety check to prevent overflow
                        if roi_y + vis_h <= output.shape[0] and roi_x + vis_w <= output.shape[1]:
                            output[roi_y:roi_y + vis_h, roi_x:roi_x + vis_w] = small_vis
                    except Exception as e:
                        # Just silently skip visualization if there's any error
                        pass
            """
        except Exception as e:
            print(f"Error visualizing detection: {e}")
            continue
    
    # Draw team counts
    try:
        # Create semi-transparent overlay for stats
        overlay = output.copy()
        # Calculate text sizes to make background fit perfectly
        fontScale = 0.4  # Even smaller font
        
        rm_size = cv2.getTextSize(f"Real Madrid: {rm_count}", cv2.FONT_HERSHEY_SIMPLEX, fontScale, 1)[0]
        barca_size = cv2.getTextSize(f"FC Barcelona: {barca_count}", cv2.FONT_HERSHEY_SIMPLEX, fontScale, 1)[0]
        ref_size = cv2.getTextSize(f"Referee: {referee_count}", cv2.FONT_HERSHEY_SIMPLEX, fontScale, 1)[0]
        
        # Find widest text
        max_width = max(rm_size[0], barca_size[0], ref_size[0])
        
        # Draw background (adjust size based on text)
        cv2.rectangle(overlay, (5, 5), (max_width + 15, 65), (0, 0, 0), -1)
        # Set transparency
        alpha = 0.5  # Even more transparent
        cv2.addWeighted(overlay, alpha, output, 1-alpha, 0, output)
        
        
        # Draw text with smaller font
        fontScale = 0.5
        cv2.putText(output, f"Real Madrid: {rm_count}", (10, 20), 
                   cv2.FONT_HERSHEY_SIMPLEX, fontScale, (255, 255, 255), 1)
        cv2.putText(output, f"FC Barcelona: {barca_count}", (10, 35), 
                   cv2.FONT_HERSHEY_SIMPLEX, fontScale, (160, 0, 140), 1)
        cv2.putText(output, f"Referee: {referee_count}", (10, 50), 
                   cv2.FONT_HERSHEY_SIMPLEX, fontScale, (0, 255, 255), 1)
        #cv2.putText(output, f"Unknown: {unknown_count}", (10, 80), 
        #           cv2.FONT_HERSHEY_SIMPLEX, fontScale, (0, 255, 0), 1)
    except Exception as e:
        print(f"Error drawing team counts: {e}")
    
    return output


####################################
#       Player Tracking Sys        #
####################################

class PlayerTracker:
    def __init__(self, memory_size=10):
        self.player_history = defaultdict(lambda: {"teams": [], "positions": []})
        self.next_id = 0
        self.memory_size = memory_size
        self.tracker = DeepSort(max_age=20)
        
    def update(self, frame, detections):
        # Convert detections to format required by DeepSort
        detection_list = []
        for det in detections:
            if det["label"] != "person":
                continue
                
            x, y, w, h = det["bbox"]
            detection_list.append(([x, y, x+w, y+h], det["confidence"], 0))  # format: (bbox, confidence, class_id)
        
        # Update tracker
        tracks = self.tracker.update_tracks(detection_list, frame=frame)
        
        # Update our tracking history
        for track in tracks:
            if not track.is_confirmed():
                continue
                
            track_id = track.track_id
            ltrb = track.to_ltrb()
            x, y, x2, y2 = ltrb
            w, h = x2-x, y2-y
            
            # Store current position
            self.player_history[track_id]["positions"].append([int(x), int(y), int(w), int(h)])
            
            # Keep only recent positions
            if len(self.player_history[track_id]["positions"]) > self.memory_size:
                self.player_history[track_id]["positions"].pop(0)
                
        return tracks
    
    def add_team_classification(self, track_id, team, confidence):
        # Add team classification to history
        self.player_history[track_id]["teams"].append((team, confidence))
        
        # Keep only recent classifications
        if len(self.player_history[track_id]["teams"]) > self.memory_size:
            self.player_history[track_id]["teams"].pop(0)
            
    def get_consistent_team(self, track_id, min_confidence=30):
        """Get temporally consistent team assignment"""
        if track_id not in self.player_history:
            return "Unknown", 0
            
        # Filter by confidence
        valid_teams = [(team, conf) for team, conf in self.player_history[track_id]["teams"] 
                      if conf >= min_confidence]
        
        if not valid_teams:
            return "Unknown", 0
            
        # Count team occurrences
        team_counts = defaultdict(int)
        team_confs = defaultdict(list)
        
        for team, conf in valid_teams:
            team_counts[team] += 1
            team_confs[team].append(conf)
            
        # Find most common team
        most_common = max(team_counts.items(), key=lambda x: x[1])
        team = most_common[0]
        
        # Average confidence for that team
        avg_conf = sum(team_confs[team]) / len(team_confs[team])
        
        return team, avg_conf






class SimpleTemporalConsistency:
    def __init__(self, memory_frames=5):
        self.memory_frames = memory_frames
        self.last_positions = []  # List of [frame_idx, x, y, w, h, team, confidence]
        
    def add_detection(self, frame_idx, x, y, w, h, team, confidence):
        self.last_positions.append([frame_idx, x, y, w, h, team, confidence])
        
        # Remove old detections
        self.last_positions = [p for p in self.last_positions 
                              if frame_idx - p[0] < self.memory_frames]
    
    def get_consistent_team(self, x, y, w, h, dist_threshold=50):
        """Get temporally consistent team for a position"""
        # Find close positions in recent frames
        close_positions = []
        center_x, center_y = x + w/2, y + h/2
        
        for pos in self.last_positions:
            _, px, py, pw, ph, team, conf = pos
            p_center_x, p_center_y = px + pw/2, py + ph/2
            
            # Calculate distance between centers
            dist = ((center_x - p_center_x)**2 + (center_y - p_center_y)**2)**0.5
            
            # If close enough, consider it the same player
            if dist < dist_threshold:
                close_positions.append((team, conf))
        
        if not close_positions:
            return None, 0
        
        # Count team occurrences
        team_counts = defaultdict(int)
        team_confs = defaultdict(list)
        
        for team, conf in close_positions:
            team_counts[team] += 1
            team_confs[team].append(conf)
        
        # Find most common team
        if not team_counts:
            return None, 0
            
        most_common = max(team_counts.items(), key=lambda x: x[1])
        team = most_common[0]
        
        # Average confidence for that team
        avg_conf = sum(team_confs[team]) / len(team_confs[team])
        
        return team, avg_conf

class TeamColorModel:
    """Builds and maintains a global model of team colors throughout the video"""
    def __init__(self, confidence_threshold=40):
        self.confidence_threshold = confidence_threshold
        # Store color samples for each team
        self.team_colors = {
            "Real Madrid": [],
            "FC Barcelona": [],
            "Referee": []
        }
        # Initialize with exemplars (will be updated as we process)
        self.team_exemplars = {
            "Real Madrid": [
                {"hsv": (0, 0, 230), "weight": 1.0},  # Pure white
                {"hsv": (80, 10, 220), "weight": 0.9}  # Off-white
            ],
            "FC Barcelona": [
                {"hsv": (105, 100, 70), "weight": 1.0},  # Dark blue
                {"hsv": (0, 120, 80), "weight": 0.9},    # Burgundy
                {"hsv": (170, 120, 80), "weight": 0.9}   # Burgundy (other end)
            ],
            "Referee": [
                {"hsv": (0, 0, 20), "weight": 1.0},      # Black
                {"hsv": (30, 150, 120), "weight": 0.9}   # Yellow
            ]
        }
        self.frame_count = 0
        
    def add_color_sample(self, team, hsv_color, confidence):
        """Add a new high-confidence color sample to the model"""
        if confidence >= self.confidence_threshold:
            self.team_colors[team].append((hsv_color, confidence))
            
            # Keep the model size manageable
            if len(self.team_colors[team]) > 50:
                self.team_colors[team].sort(key=lambda x: x[1], reverse=True)
                self.team_colors[team] = self.team_colors[team][:50]




######################################
#          Ball Tracker              #
######################################
class BallTracker:
    def __init__(self, memory_frames=10):
        self.positions = []  # List of (frame_idx, x, y, w, h)
        self.memory_frames = memory_frames
        
    def update(self, frame_idx, ball_detection):
        if ball_detection:
            x, y, w, h = ball_detection["bbox"]
            self.positions.append((frame_idx, x, y, w, h))
        
        # Remove old positions
        self.positions = [p for p in self.positions if frame_idx - p[0] < self.memory_frames]
        
    def get_smoothed_position(self):
        """Get smoothed ball position using recent history"""
        if not self.positions:
            return None
            
        # Use recent positions for smoothing
        recent = self.positions[-min(5, len(self.positions)):]
        x = sum(p[1] for p in recent) / len(recent)
        y = sum(p[2] for p in recent) / len(recent)
        w = sum(p[3] for p in recent) / len(recent)
        h = sum(p[4] for p in recent) / len(recent)
        
        return int(x), int(y), int(w), int(h)

def determine_ball_possession(player_detections, ball_pos, max_distance=150, debug=False):
    """Improved ball possession detection with debugging"""
    if not ball_pos:
        return None
        
    ball_x, ball_y = ball_pos[0] + ball_pos[2]/2, ball_pos[1] + ball_pos[3]/2
    
    if debug:
        print(f"Ball position: ({ball_x:.1f}, {ball_y:.1f})")
        print(f"Checking {len(player_detections)} players for possession")
    
    # Find nearby players
    nearby_players = []
    
    for i, player in enumerate(player_detections):
        if "team" not in player:
            if debug:
                print(f"Player {i} has no team attribute")
            continue
            
        # Player center
        x, y, w, h = player["bbox"]
        player_x, player_y = x + w/2, y + h/2
        player_bottom = y + h  # Bottom of player bounding box
        
        # Distance to ball
        distance = ((ball_x - player_x)**2 + (ball_y - player_y)**2)**0.5
        
        if debug and distance < 200:
            print(f"Player {i} ({player['team']}): distance={distance:.1f}, position=({player_x:.1f}, {player_y:.1f})")
        
        # Check if ball is near player's feet (better indicator for possession)
        foot_proximity = abs(ball_y - player_bottom)
        foot_horizontal = abs(ball_x - player_x)
        
        # Add distance and team info to nearby_players
        if distance < max_distance:
            # Prioritize players whose feet are near the ball
            foot_score = max(0, 1.0 - (foot_proximity / 100))
            # Closer horizontally to player center = better
            horizontal_score = max(0, 1.0 - (foot_horizontal / 50))
            
            effective_distance = distance * (1.0 - 0.3*foot_score - 0.2*horizontal_score)
            
            nearby_players.append({
                "team": player["team"],
                "distance": distance,
                "effective_distance": effective_distance,
                "foot_proximity": foot_proximity
            })
    
    if not nearby_players:
        if debug and ball_pos:
            print("No players near ball")
        return None
        
    # Sort by effective distance (incorporating foot proximity)
    nearby_players.sort(key=lambda p: p["effective_distance"])
    
    if debug:
        print(f"Nearest player: {nearby_players[0]['team']} at distance {nearby_players[0]['distance']:.1f}")
    
    # If a player is significantly closer than others, they have possession
    if len(nearby_players) >= 2:
        if nearby_players[0]["distance"] < nearby_players[1]["distance"] * 0.7:
            if debug:
                print(f"Clear possession by {nearby_players[0]['team']}")
            return nearby_players[0]["team"]
    
    # Even if not clearly closer than others, return closest player's team
    return nearby_players[0]["team"]

#######################################
#      Main Processing Loop          #
#######################################

# Main processing loop
if __name__ == "__main__":
    # Path to color frames
    frames_filename = "preprocessed_frames_P1_colored.npz"
    
    # Create window
    cv2.namedWindow("Team Classification", cv2.WINDOW_NORMAL)
    cv2.resizeWindow("Team Classification", 960, 540)
    
    # Load frames
    if os.path.exists(frames_filename):
        frames, fps = load_preprocessed_frames(frames_filename)
        print(f"Frame shape: {frames[0].shape}")
    else:
        print("Color frames file not found!")
        exit(1)
    
    # Load YOLOv8 for detection
    model = YOLO('yolov8n.pt')
    
    # Create temporal consistency tracker for player classification
    temporal_consistency = SimpleTemporalConsistency(memory_frames=15)
    
    # Create ball tracker
    ball_tracker = BallTracker(memory_frames=15)
    
    # Create video writer
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out_writer = cv2.VideoWriter("team_classification_presentation.mp4", fourcc, fps, 
                                (frames[0].shape[1], frames[0].shape[0]))
    
    # Settings for presentation
    debug_frequency = 50  # Reduce debug output frequency
    possession_distance = 200  # Increase distance threshold for possession
    play_speed = 150  # Slightly slower for better viewing
    
    print("Processing frames...")
    # Process frames
    for idx, frame in enumerate(frames):
        try:
            # Skip frames for faster processing during testing
            if idx % 5 != 0:
                continue
                         
            # Detect players and ball
            detections = detect_objects(frame, model)
            
            # Separate player and ball detections
            player_detections = [d for d in detections if d["label"] == "person"]
            ball_detections = [d for d in detections if d["label"] == "sports ball"]
    
            # Get ball position (if detected)
            ball_detection = ball_detections[0] if ball_detections else None
            
            # Update ball tracker
            ball_tracker.update(idx, ball_detection)
            
            # Get smoothed ball position
            smoothed_ball = ball_tracker.get_smoothed_position()
            
            # Add frame index to each detection for temporal consistency
            for det in player_detections:
                det["frame_idx"] = idx
            
            # Enhanced processing with temporal consistency - PRESENTATION MODE
            output = visualize_teams(frame, player_detections, 
                                    temporal_consistency=temporal_consistency,
                                    show_debug=False)  # Turn off debug visuals
            
            # Count how many players have team attribute (debug only)
            # players_with_team = sum(1 for p in player_detections if "team" in p)
            # if idx % debug_frequency == 0:
            #    print(f"Frame {idx}: {len(player_detections)} players, {players_with_team} with team classification")
            
            # Determine ball possession AFTER team classification
            ball_possession = determine_ball_possession(player_detections, smoothed_ball, 
                                          max_distance=possession_distance, 
                                          debug=False)  # Turn off debug output
            
            # Visualize ball if detected - BEAUTIFIED VERSION
            if smoothed_ball:
                x, y, w, h = smoothed_ball
                # Draw ball with possession info
                possession_color = (255, 0, 0)  # Blue when no possession
                if ball_possession == "Real Madrid":
                    possession_color = (255, 255, 255)
                elif ball_possession == "FC Barcelona":
                    possession_color = (160, 0, 140)
                elif ball_possession == "Referee":
                    possession_color = (0, 255, 255)

                # Make ball visualization more elegant
                ball_cx, ball_cy = x+w//2, y+h//2
                ball_radius = max(4, w//2)  # Slightly smaller radius
    
                # Draw a subtle glow effect
                for i in range(2):  # Reduced glow for cleaner look
                    radius = ball_radius + i
                    alpha = 0.15 - (i * 0.05)  # More subtle glow
                    overlay = output.copy()
                    cv2.circle(overlay, (ball_cx, ball_cy), radius, possession_color, 1)
                    cv2.addWeighted(overlay, alpha, output, 1-alpha, 0, output)
    
                # Draw main ball circle
                cv2.circle(output, (ball_cx, ball_cy), ball_radius, possession_color, 1)
    
                # Draw line from ball to closest player
                if ball_possession:
                    # Find closest player by team
                    closest_player = None
                    min_dist = float('inf')
        
                    for player in player_detections:
                        if "team" not in player or player["team"] != ball_possession:
                            continue
                
                        px, py, pw, ph = player["bbox"]
                        player_cx, player_cy = px+pw//2, py+ph//2
                        dist = ((ball_cx - player_cx)**2 + (ball_cy - player_cy)**2)**0.5
            
                        if dist < min_dist:
                            min_dist = dist
                            closest_player = (player_cx, player_cy)
        
                    if closest_player:
                        # Draw elegant dashed line (fewer dashes for cleaner look)
                        pt1 = (ball_cx, ball_cy)
                        pt2 = closest_player
                        dist = int(((pt1[0]-pt2[0])**2 + (pt1[1]-pt2[1])**2)**0.5)
            
                        # Create dash pattern with larger spacing
                        dash_length = 5
                        for i in range(0, dist, dash_length*3):  # More spacing between dashes
                            start_point = (
                                int(pt1[0] + (pt2[0] - pt1[0]) * i / dist),
                                int(pt1[1] + (pt2[1] - pt1[1]) * i / dist)
                            )
                            end_point = (
                                int(pt1[0] + (pt2[0] - pt1[0]) * min(i + dash_length, dist) / dist),
                                int(pt1[1] + (pt2[1] - pt1[1]) * min(i + dash_length, dist) / dist)
                            )
                            cv2.line(output, start_point, end_point, possession_color, 1)

                    # Show possession with minimal visibility - moved near the ball
                    if ball_possession:
                        # Draw small indicator near the ball instead of corner
                        text = f"Ball: {ball_possession}"
                        text_size = cv2.getTextSize(text, cv2.FONT_HERSHEY_SIMPLEX, 0.4, 1)[0]
            
                        # Semi-transparent background - position above the ball
                        overlay = output.copy()
                        bg_y = max(0, ball_cy - ball_radius - 20)
                        cv2.rectangle(overlay, 
                                     (ball_cx - text_size[0]//2 - 5, bg_y), 
                                     (ball_cx + text_size[0]//2 + 5, bg_y + 15), 
                                     (0, 0, 0), -1)
                        cv2.addWeighted(overlay, 0.5, output, 0.5, 0, output)
            
                        # Draw text
                        cv2.putText(output, text, 
                                   (ball_cx - text_size[0]//2, bg_y + 11),
                                   cv2.FONT_HERSHEY_SIMPLEX, 0.4, possession_color, 1)
            
            # Write and display
            out_writer.write(output)
            display_frame = cv2.resize(output, (960, 540))
            cv2.imshow("Team Classification", display_frame)
            
            # Process UI events (slow down playback)
            key = cv2.waitKey(play_speed)
            if key == 27:  # ESC
                break
            elif key == 32:  # SPACE - pause
                cv2.waitKey(0)  # Wait indefinitely until another key is pressed
            
            # Progress update (less frequent)
            if idx % 50 == 0:
                print(f"Processed frame {idx}")
                
        except Exception as e:
            print(f"Error on frame {idx}: {e}")
            import traceback
            traceback.print_exc()
            continue
            
    # Clean up
    out_writer.release()
    cv2.destroyAllWindows()
    print("Complete! Output saved to team_classification_presentation.mp4")

Loaded 9501 frames from preprocessed_frames_P1_colored.npz
Frame shape: (360, 640, 3)
Processing frames...

0: 384x640 3 persons, 67.7ms
Speed: 8.8ms preprocess, 67.7ms inference, 3.0ms postprocess per image at shape (1, 3, 384, 640)
Dominant color: H:112.0 S:144.0 V:53.0 - 65.1%
Real Madrid score: 143.8
FC Barcelona score: 232.7
Referee score: 145.9
Dominant color: H:109.0 S:78.0 V:88.0 - 49.1%
Real Madrid score: 141.1
FC Barcelona score: 164.9
Referee score: 126.8
Dominant color: H:105.0 S:165.0 V:51.0 - 45.9%
Dominant color: H:111.0 S:59.0 V:90.0 - 31.0%
Real Madrid score: 120.5
FC Barcelona score: 188.9
Referee score: 117.9
Processed frame 0

0: 384x640 3 persons, 55.2ms
Speed: 1.1ms preprocess, 55.2ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)
Dominant color: H:103.0 S:105.0 V:56.0 - 62.8%
Real Madrid score: 152.3
FC Barcelona score: 212.1
Referee score: 144.2
Dominant color: H:98.0 S:121.0 V:55.0 - 71.4%
Real Madrid score: 152.6
FC Barcelona score: 233.0
Ref